The implementation of the code for this project builds upon the work from several repositories and the knowledge gained from tutorials conducted during the term. The key repositories utilized are as follows:
- \url{https://github.com/ralphabb/GNN-RNI.git}
- \url{https://github.com/KarolisMart/DropGNN.git}
- \url{https://anonymous.4open.science/r/CoGNN}

In [ ]:
%%capture
%env TORCH=2.1.0+cu121
!pip install torch_scatter torch_sparse torch_spline_conv -f https://data.pyg.org/whl/torch-${TORCH}.html
!pip install torchmetrics ogb rdkit
!pip install torch-geometric

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
from typing import Tuple

from torch import Tensor
from torch.nn import Module, Dropout, LayerNorm, Identity
from torch_geometric.data import DataLoader, Data, InMemoryDataset
from torch_geometric.nn import GINConv, GINEConv, global_add_pool
from torch_geometric.typing import Adj, OptTensor
from torch_geometric.utils import degree
from torch_geometric.utils.convert import from_networkx

from google.colab import drive


In [ ]:
# This will prompt for authorization and mount your entire Google Drive
drive.mount('/content/drive', force_remount = True)
%cd /content/drive/My Drive/Co-GNN

Mounted at /content/drive
/content/drive/My Drive/Co-GNN


Due to a recent update in Torch Geometric, the EXP dataset in pickle and .pt format from the original repository is no longer directly compatible. To address this, I have reconstructed the dataset and successfully imported it into this notebook.

In [ ]:
data, slices = torch.load('exp_dataset.pt')

In [ ]:
class PlanarSATPairsDataset(InMemoryDataset):
    def __init__(self):
        super(PlanarSATPairsDataset, self).__init__()
        self.data, self.slices = data, slices
exp_dataset = PlanarSATPairsDataset()

Several experiments were conducted using the specified triangles dataset, but these were not included in the final paper due to space constraints.

In [ ]:
class SymmetrySet:
    def __init__(self):
        self.hidden_units = 0
        self.num_classes = 0
        self.num_features = 0
        self.num_nodes = 0

    def addports(self, data):
        data.ports = torch.zeros(data.num_edges, 1)
        degs = degree(data.edge_index[0], data.num_nodes, dtype=torch.long) # out degree of all nodes
        for n in range(data.num_nodes):
            deg = degs[n]
            ports = np.random.permutation(int(deg))
            for i, neighbor in enumerate(data.edge_index[1][data.edge_index[0]==n]):
                nb = int(neighbor)
                data.ports[torch.logical_and(data.edge_index[0]==n, data.edge_index[1]==nb), 0] = float(ports[i])
        return data

    def makefeatures(self, data):
        data.x = torch.ones((data.num_nodes, 1))
        data.id = torch.tensor(np.random.permutation(np.arange(data.num_nodes))).unsqueeze(1)
        return data

    def makedata(self):
        pass

class Triangles(SymmetrySet):
    def __init__(self):
        super().__init__()
        self.hidden_units = 16
        self.num_classes = 2
        self.num_features = 1
        self.num_nodes = 60
        self.graph_class = False

    def makedata(self):
        size = self.num_nodes
        generated = False
        while not generated:
            nx_g = nx.random_degree_sequence_graph([3] * size)
            data = from_networkx(nx_g)
            labels = [0] * size
            for n in range(size):
                for nb1 in data.edge_index[1][data.edge_index[0]==n]:
                    for nb2 in data.edge_index[1][data.edge_index[0]==n]:
                        if torch.logical_and(data.edge_index[0]==nb1, data.edge_index[1]==nb2).any():
                            labels[n] = 1
            generated = labels.count(0) >= 20 and labels.count(1) >= 20
        data.y = torch.tensor(labels)

        data = self.addports(data)
        data = self.makefeatures(data)
        return [data]
triangles_dataset = Triangles()


## Models


In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

### Co-GNNs

In [ ]:
from models.CoGNN import CoGNN

from helpers.model import ModelType
from helpers.classes import Pool
from helpers.metrics import MetricType
from helpers.classes import ActivationType, Pool, ModelType
from helpers.encoders import DataSetEncoders, PosEncoder
from lrgb.cosine_scheduler import cosine_with_warmup_scheduler
from lrgb.transforms import apply_transform

from helpers.classes import GumbelArgs, EnvArgs, ActionNetArgs, Pool, DataSetEncoders
from models.temp import TempSoftPlus
from models.action import ActionNet


params_cognn = {
    "dataset": None,
    "pool": Pool.MEAN,
    "learn_temp": False,
    "temp_model_type": ModelType.LIN,
    "tau0": 0.5,
    "temp": 0.01,
    "max_epochs": 3000,
    "batch_size": 32,
    "lr": 1e-3,
    "dropout": 0.2,
    "env_model_type": ModelType.MEAN_GNN,
    "env_num_layers": 3,
    "env_dim": 128,
    "in_dim" : 2,
    'out_dim' : 2,
    "skip": False,
    "batch_norm": False,
    "layer_norm": False,
    "dec_num_layers": 1,
    "pos_enc": PosEncoder.NONE,
    "act_model_type": ModelType.MEAN_GNN,
    "act_num_layers": 1,
    "act_dim": 16,
    "seed": 0,
    "gpu": None,
    "fold": None,
    "weight_decay": 0,
    "step_size": None,
    "gamma": None,
    "num_warmup_epochs": None,
    "dataset_encoder" : DataSetEncoders.NONE,
    "metric_type" : MetricType.ACCURACY,
    'env_act_type': ActivationType.RELU,
    'act_type' : ActivationType.RELU
}


/usr/local/lib/python3.10/dist-packages/torch_geometric/graphgym/config.py:19: UserWarning: Could not define global config object. Please install 'yacs' via 'pip install yacs' in order to use GraphGym
  warnings.warn("Could not define global config object. Please install "
/usr/local/lib/python3.10/dist-packages/torch_geometric/graphgym/imports.py:14: UserWarning: Please install 'pytorch_lightning' via  'pip install pytorch_lightning' in order to use GraphGym
  warnings.warn("Please install 'pytorch_lightning' via  "


In [ ]:
def gin_mlp_func(in_channels: int, out_channels: int, bias: bool):
                return torch.nn.Sequential(torch.nn.Linear(in_channels, 2 * in_channels, bias=bias),
                                           torch.nn.BatchNorm1d(2 * in_channels),
                                           torch.nn.ELU(), torch.nn.Linear(2 * in_channels, out_channels, bias=bias))



MLP class and Random Node Initializer used throughout the notebook.

In [ ]:
class RNInit(nn.Module):

    def __init__(self, random_dims = 1, distribution = 'n'):
        super().__init__()
        self.random_dims = random_dims
        self.distribution = distribution

    def forward(self, x):
        if self.random_dims > 0:

            rand = torch.empty(( x.shape[0], self.random_dims)).to(device)
            if self.distribution == "n":
                torch.nn.init.normal_(rand)
            elif self.distribution == "u":
                torch.nn.init.uniform_(rand, a=-1.0, b=1.0)
            elif self.distribution == "xn":
                torch.nn.init.xavier_normal_(rand)
            elif self.distribution == "xu":
                torch.nn.init.xavier_uniform_(rand)
            elif self.distribution == 'ones':
               torch.nn.init.ones_(rand)
            x = torch.cat([x, rand], dim=1).to(device)
        return x


class MLPModule(nn.Module):
    def __init__(self, hidden_dim, output_dim = 2, activation=nn.ELU(), dropout_p=0):
        super().__init__()
        layers = []
        layers.extend([torch.nn.Linear(hidden_dim, hidden_dim), activation, nn.Dropout(dropout_p)])
        layers.extend([torch.nn.Linear(hidden_dim, 32),activation])
        layers.append(torch.nn.Linear(32, output_dim))

        self.layers_sequential = nn.Sequential(*layers)

    def forward(self, x):
        return F.log_softmax(self.layers_sequential(x), dim=1)

    @staticmethod
    def _weight_reset(module):
        if isinstance(module, nn.Linear):
            module.reset_parameters()

    def reset_parameters(self):
        return self.layers_sequential.apply(type(self)._weight_reset)



In [ ]:
class CoGNN(Module):
    def __init__(self,params_cognn = params_cognn, rni = RNInit(random_dims = 0)):

        super(CoGNN, self).__init__()
        self.rni = rni
        gumbel_args = GumbelArgs(
                                  learn_temp=params_cognn["learn_temp"],
                                  temp_model_type=params_cognn["temp_model_type"],
                                  tau0=params_cognn["tau0"],
                                  temp=params_cognn["temp"],
                                  gin_mlp_func=gin_mlp_func
                              )
        env_args = EnvArgs(
                                  model_type=params_cognn["env_model_type"],
                                  num_layers=params_cognn["env_num_layers"],
                                  env_dim=params_cognn["env_dim"],
                                  layer_norm=params_cognn["layer_norm"],
                                  skip=params_cognn["skip"],
                                  batch_norm=params_cognn["batch_norm"],
                                  dropout=params_cognn["dropout"],
                                  act_type=params_cognn['env_act_type'],
                                  metric_type=params_cognn["metric_type"],
                                  in_dim=params_cognn["in_dim"] + rni.random_dims,
                                  out_dim=params_cognn['out_dim'],
                                  gin_mlp_func=gin_mlp_func,
                                  dec_num_layers=params_cognn["dec_num_layers"],
                                  pos_enc=params_cognn["pos_enc"],
                                  dataset_encoders=params_cognn["dataset_encoder"]
            )
        action_args = ActionNetArgs(
                                  model_type=params_cognn["act_model_type"],
                                  num_layers=params_cognn["act_num_layers"],
                                  hidden_dim=params_cognn["act_dim"],
                                  dropout=params_cognn["dropout"],
                                  act_type=params_cognn['act_type'],
                                  env_dim=params_cognn["env_dim"],
                                  gin_mlp_func=gin_mlp_func
                              )
        self.learn_temp = gumbel_args.learn_temp
        if gumbel_args.learn_temp:
            self.temp_model = TempSoftPlus(gumbel_args=gumbel_args, env_dim=env_args.env_dim)
        self.temp = gumbel_args.temp

        self.num_layers = env_args.num_layers
        self.env_net = env_args.load_net()
        self.use_encoders = env_args.dataset_encoders.use_encoders()

        layer_norm_cls = LayerNorm if env_args.layer_norm else Identity
        self.hidden_layer_norm = layer_norm_cls(env_args.env_dim)
        self.skip = env_args.skip
        self.dropout = Dropout(p=env_args.dropout)
        self.drop_ratio = env_args.dropout
        self.act = env_args.act_type.get()
        self.in_act_net = ActionNet(action_args=action_args)
        self.out_act_net = ActionNet(action_args=action_args)

        # Encoder types
        self.dataset_encoder = env_args.dataset_encoders
        self.env_bond_encoder = self.dataset_encoder.edge_encoder(emb_dim=env_args.env_dim, model_type=env_args.model_type)
        self.act_bond_encoder = self.dataset_encoder.edge_encoder(emb_dim=action_args.hidden_dim, model_type=action_args.model_type)

        # Pooling function to generate whole-graph embeddings
        self.pooling = params_cognn['pool'].get()

    def forward(self, data, pestat = None, edge_attr: OptTensor = None,  # x is rni(data.x) y batch = data.batch
                edge_ratio_node_mask: OptTensor = None) -> Tuple[Tensor, Tensor]:
        result = 0
        x = self.rni(data.x)
        edge_index = data.edge_index
        batch = data.batch
        calc_stats = edge_ratio_node_mask is not None
        if calc_stats:
            edge_ratio_edge_mask = edge_ratio_node_mask[edge_index[0]] & edge_ratio_node_mask[edge_index[1]]
            edge_ratio_list = []

        # bond encode
        if edge_attr is None or self.env_bond_encoder is None:
            env_edge_embedding = None
        else:
            env_edge_embedding = self.env_bond_encoder(edge_attr)
        if edge_attr is None or self.act_bond_encoder is None:
            act_edge_embedding = None
        else:
            act_edge_embedding = self.act_bond_encoder(edge_attr)

        # node encode
        x = self.env_net[0](x, pestat)  # (N, F) encoder
        if not self.use_encoders:
            x = self.dropout(x)
            x = self.act(x)

        for gnn_idx in range(self.num_layers):
            x = self.hidden_layer_norm(x)

            # action
            in_logits = self.in_act_net(x=x, edge_index=edge_index, env_edge_attr=env_edge_embedding,
                                        act_edge_attr=act_edge_embedding)  # (N, 2)
            out_logits = self.out_act_net(x=x, edge_index=edge_index, env_edge_attr=env_edge_embedding,
                                          act_edge_attr=act_edge_embedding)  # (N, 2)

            temp = self.temp_model(x=x, edge_index=edge_index,
                                   edge_attr=env_edge_embedding) if self.learn_temp else self.temp
            in_probs = F.gumbel_softmax(logits=in_logits, tau=temp, hard=True)
            out_probs = F.gumbel_softmax(logits=out_logits, tau=temp, hard=True)
            edge_weight = self.create_edge_weight(edge_index=edge_index,
                                                  keep_in_prob=in_probs[:, 0], keep_out_prob=out_probs[:, 0])

            # environment
            out = self.env_net[1 + gnn_idx](x=x, edge_index=edge_index, edge_weight=edge_weight,
                                            edge_attr=env_edge_embedding)
            out = self.dropout(out)
            out = self.act(out)

            if calc_stats:
                edge_ratio = edge_weight[edge_ratio_edge_mask].sum() / edge_weight[edge_ratio_edge_mask].shape[0]
                edge_ratio_list.append(edge_ratio.item())

            if self.skip:
                x = x + out
            else:
                x = out

        x = self.hidden_layer_norm(x)
        x = self.pooling(x, batch=batch)
        x = self.env_net[-1](x)  # decoder
        result = result + x

        if calc_stats:
            edge_ratio_tensor = torch.tensor(edge_ratio_list, device=x.device)
        else:
            edge_ratio_tensor = -1 * torch.ones(size=(self.num_layers,), device=x.device)
        return F.log_softmax(result, dim = 1), edge_ratio_tensor    # WE HAVE ADDED THE LOG_SOFTMAX, TO GO SIMILAR TO THE REST

    def create_edge_weight(self, edge_index: Adj, keep_in_prob: Tensor, keep_out_prob: Tensor) -> Tensor:
        u, v = edge_index
        edge_in_prob = keep_in_prob[v]
        edge_out_prob = keep_out_prob[u]
        return edge_in_prob * edge_out_prob

    def reset_parameters(self):
        for module in self.modules():
            # Skip the first module, which is the rGCN module itself
            if module != self:
                # Check if the module has 'reset_parameters' method
                if hasattr(module, 'reset_parameters'):
                    module.reset_parameters()


## RNI MODELS

In [ ]:
from torch_geometric.nn import GraphConv
from torch_scatter import scatter_max, scatter_mean

class rGCN(torch.nn.Module):
    def __init__(self, dataset_dim = 2,  hidden_dim = 64, num_layers = 8,  activation = nn.ELU(), pooling = 'max',  rni = RNInit()):
        super(rGCN, self).__init__()

        self.layers = torch.nn.ModuleList()
        input_dim = dataset_dim + rni.random_dims
        self.layers.append(GraphConv(input_dim, hidden_dim, norm = True))
        for layer in range(num_layers - 1):
            self.layers.append(GraphConv(hidden_dim, hidden_dim, norm=True))
        self.mlp = MLPModule(hidden_dim = hidden_dim, output_dim = 2, activation = activation, dropout_p = 0.5)
        self.num_layers = num_layers
        self.activation = activation
        self.scatter = pooling
        self.rni = rni

    def reset_parameters(self):
        for module in self.modules():
            # Skip the first module, which is the rGCN module itself
            if module != self:
                # Check if the module has 'reset_parameters' method
                if hasattr(module, 'reset_parameters'):
                    module.reset_parameters()

    def forward(self, data):
        x = self.rni(data.x)
        for layer in self.layers:  # Number of message passing iterations we want to test over
            x = self.activation(layer(x, data.edge_index))
        x = self.pooling(x, data.batch)
        return self.mlp(x)

    def pooling(self, x_feat, batch):
        if self.scatter == "max":
            return scatter_max(x_feat, batch, dim=0)[0]
        elif self.scatter == "mean":
            return scatter_mean(x_feat, batch, dim=0)
        else:
            pass



In [ ]:
from torch_geometric.nn import MessagePassing
class GINConv(MessagePassing):
    def __init__(self, emb_dim, output_dim = None, aggr = 'add', activation = nn.ReLU()):
        '''
            emb_dim (int): node embedding dimensionality
        '''
        super(GINConv, self).__init__(aggr)
        if output_dim == None:
          output_dim = emb_dim
        self.mlp = torch.nn.Sequential(torch.nn.Linear(emb_dim, 2*emb_dim), torch.nn.BatchNorm1d(2*emb_dim), activation, torch.nn.Linear(2*emb_dim, output_dim))
        self.eps = torch.nn.Parameter(torch.Tensor([0]))

    def forward(self, x, edge_index):
        out = self.mlp((1 + self.eps) *x + self.propagate(edge_index, x=x))
        return out

    def message(self, x_j):
        return F.relu(x_j)

    def update(self, aggr_out):
        return aggr_out


### GNN to generate node embedding
class rGIN(torch.nn.Module):
    """
    Output:
        node representations
    """
    def __init__(self, num_layers = 8, dataset_dim = 2, hidden_dim = 64, activation = nn.ELU(), drop_ratio = 0.5, JK = "last", residual = False, aggr = 'add', pooling = 'max', rni = RNInit()):
        '''
            emb_dim (int): node embedding dimensionality
            num_layer (int): number of GNN message passing layers
        '''
        super(rGIN, self).__init__()
        self.num_layers = num_layers
        if self.num_layers < 2:
            raise ValueError("Number of GNN layers must be greater than 1.")

        self.layers = nn.ModuleList()
        self.batch_norms = torch.nn.ModuleList()
        self.rni = rni

        self.layers.append(GINConv(dataset_dim + rni.random_dims, hidden_dim, aggr = aggr))
        self.batch_norms.append(torch.nn.BatchNorm1d(hidden_dim))
        for layer in range(num_layers - 1):
            self.layers.append(GINConv(hidden_dim, aggr = aggr))
            self.batch_norms.append(torch.nn.BatchNorm1d(hidden_dim))

        self.mlp = MLPModule(hidden_dim = hidden_dim, output_dim = 2, activation = activation, dropout_p = drop_ratio)
        self.activation = activation
        self.scatter = pooling
        self.drop_ratio = drop_ratio

    def reset_parameters(self):
        for module in self.modules():
            # Skip the first module, which is the rGCN module itself
            if module != self:
                # Check if the module has 'reset_parameters' method
                if hasattr(module, 'reset_parameters'):
                    module.reset_parameters()

    def forward(self, data):
        x = self.rni(data.x)
        for layer in range(self.num_layers):
            x = self.layers[layer](x, data.edge_index)
            x = self.batch_norms[layer](x)
           # x = F.dropout(x, self.drop_ratio, training = self.training)
        x = self.pooling(x, data.batch)
        return self.mlp(x)

    def pooling(self, x_feat, batch):
        if self.scatter == "max":
            return scatter_max(x_feat, batch, dim=0)[0]
        elif self.scatter == "mean":
            return scatter_mean(x_feat, batch, dim=0)
        else:
            pass


In [ ]:
from torch_geometric.nn import global_add_pool
import random
class DropGIN(nn.Module):
        def __init__(self, dataset, num_layers = 8, hidden_dim = 64, num_features = 2, use_aux_loss = False, num_runs = 20, p = 1/20, augmentation = False):
            super(DropGIN, self).__init__()


            dim = hidden_dim
            self.num_layers = num_layers
            self.num_runs = num_runs
            self.p = p
            self.use_aux_loss = use_aux_loss
            self.random_value = random.uniform(0, 0.5)
            self.augmentation = augmentation
            self.Conv = GINConv

            self.convs = nn.ModuleList()
            self.bns = nn.ModuleList()
            self.fcs = nn.ModuleList()

            self.convs.append(GINConv(num_features, hidden_dim))
            self.bns.append(nn.BatchNorm1d(dim))
            self.fcs.append(nn.Linear(num_features, dataset.num_classes))
            self.fcs.append(nn.Linear(dim, dataset.num_classes))

            for i in range(self.num_layers-1):
                self.convs.append(GINConv(hidden_dim))
                self.bns.append(nn.BatchNorm1d(dim))
                self.fcs.append(nn.Linear(dim, dataset.num_classes))

            if use_aux_loss:
                self.aux_fcs = nn.ModuleList()
                self.aux_fcs.append(nn.Linear(num_features, dataset.num_classes))
                for i in range(self.num_layers):
                    self.aux_fcs.append(nn.Linear(dim, dataset.num_classes))

        def reset_parameters(self):
            for m in self.modules():
                if isinstance(m, nn.Linear):
                    m.reset_parameters()
                elif isinstance(m, self.Conv):
                    m.reset_parameters()
                elif isinstance(m, nn.BatchNorm1d):
                    m.reset_parameters()

        def forward(self, data):
            x = data.x
            edge_index = data.edge_index
            batch = data.batch

            # Do runs in paralel, by repeating the graphs in the batch
            x = x.unsqueeze(0).expand(self.num_runs, -1, -1).clone()
            drop = torch.bernoulli(torch.ones([x.size(0), x.size(1)], device=x.device) * self.p).bool()
            if self.augmentation == 'rrni':
                x[drop] = self.random_value
            else:
                x[drop] = 0.0
            del drop
            outs = [x]
            x = x.view(-1, x.size(-1))
            run_edge_index = edge_index.repeat(1, self.num_runs) + torch.arange(self.num_runs, device=edge_index.device).repeat_interleave(edge_index.size(1)) * (edge_index.max() + 1)
            for i in range(self.num_layers):
                x = self.convs[i](x, run_edge_index)
                x = self.bns[i](x)
                x = F.elu(x)
                outs.append(x.view(self.num_runs, -1, x.size(-1)))
            del run_edge_index

            out = None
            for i, x in enumerate(outs):
                x = x.mean(dim=0)


                x =  scatter_max(x, batch, dim=0)[0]
                x = self.fcs[i](x) # No dropout layer in these experiments
                if out is None:
                    out = x
                else:
                    out += x

            if self.use_aux_loss:
                aux_out = torch.zeros(self.num_runs, out.size(0), out.size(1), device=out.device)
                run_batch = batch.repeat(self.num_runs) + torch.arange(self.num_runs, device=edge_index.device).repeat_interleave(batch.size(0)) * (batch.max() + 1)
                for i, x in enumerate(outs):
                    x = x.view(self.num_runs, -1, x.size(-1))
                    x = self.aux_fcs[i](x) # No dropout layer in these experiments
                    aux_out += x

                return F.log_softmax(out, dim=-1), F.log_softmax(aux_out, dim=-1)
            else:
                return F.log_softmax(out, dim=-1)  ### We have modified the output to be just one element.

##TRAIN/TEST FUNCTIONS

In [ ]:
def train(model, epoch, loader, optimizer):
    model.train()
    loss_all = 0

    for data in loader:
        data = data.to(device)
        optimizer.zero_grad()
        if isinstance(model, CoGNN):
          output, _ = model(data)
          loss = F.nll_loss(output, data.y)
        else:
          loss = F.nll_loss(model(data), data.y)
        loss.backward()
        loss_all += data.num_graphs * loss.item()
        # torch.nn.utils.clip_grad_norm_(model.parameters(), CLIP)
        optimizer.step()
    return loss_all / len(loader.dataset)


def val(model, loader):
    model.eval()
    loss_all = 0

    for data in loader:
        data = data.to(device)
        if isinstance(model, CoGNN):
          output, _ = model(data)
          loss_all += F.nll_loss(output, data.y, reduction='sum').item()
        else:
          loss_all += F.nll_loss(model(data), data.y, reduction='sum').item()
    return loss_all / len(loader.dataset)


def test(model, loader):
    model.eval()
    correct = 0
    with torch.no_grad():
      for data in loader:
          data = data.to(device)
          nb_trials = 1   # Support majority vote, but single trial is default
          successful_trials = torch.zeros_like(data.y)
          for i in range(nb_trials):  # Majority Vote
              if isinstance(model, CoGNN):
                output, _ = model(data)
                pred = output.max(1)[1]
              else:
                pred = model(data).max(1)[1]
              successful_trials += pred.eq(data.y)
          successful_trials = successful_trials > (nb_trials // 2)
          correct += successful_trials.sum().item()
    return correct / len(loader.dataset)


In [ ]:


def train_model(model, dataset = exp_dataset, epochs = 300, learning_rate=0.001, batch_size=20, splits=10, modulo=4, mod_thresh=1):
    tr_accuracies = np.zeros((epochs, splits))
    tst_accuracies = np.zeros((epochs, splits))
    tst_exp_accuracies = np.zeros((epochs, splits))
    tst_lrn_accuracies = np.zeros((epochs, splits))
    acc = []
    tr_acc = []

    for i in range(splits):
        model.reset_parameters()
        optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
        scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
            optimizer, mode='min', factor=0.7, patience=5, min_lr=learning_rate)

        n = len(dataset) // splits
        test_mask = torch.zeros(len(dataset), dtype=torch.bool)
        test_mask[i * n:(i + 1) * n] = 1
        learning_indices = torch.where((torch.arange(len(dataset)) % modulo <= mod_thresh) & ~test_mask)[0]
        exp_indices = torch.where((torch.arange(len(dataset)) % modulo > mod_thresh) & ~test_mask)[0]

        # Convert boolean masks to lists of indices
        test_indices = test_mask.nonzero(as_tuple=False).view(-1).tolist()
        learning_indices = learning_indices.tolist()
        exp_indices = exp_indices.tolist()

        # Now load the datasets using lists of indices
        test_dataset = [dataset[idx] for idx in test_indices]
        test_exp_dataset = [dataset[idx] for idx in exp_indices]
        test_lrn_dataset = [dataset[idx] for idx in learning_indices]
        train_dataset = [dataset[idx] for idx in range(len(dataset)) if idx not in test_indices]

        # Creating data loaders
        val_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
        test_loader = DataLoader(test_dataset, batch_size=batch_size)
        test_exp_loader = DataLoader(test_exp_dataset, batch_size=batch_size)
        test_lrn_loader = DataLoader(test_lrn_dataset, batch_size=batch_size)
        train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

        print('---------------- Split {} ----------------'.format(i))
        best_val_loss, test_acc = 100, 0
        for epoch in range(epochs):
            lr = scheduler.optimizer.param_groups[0]['lr']
            train_loss = train(model, epoch, train_loader, optimizer)  # Assuming train is a predefined function
            val_loss = val(model, val_loader)  # Assuming val is a predefined function
            scheduler.step(val_loss)
            if best_val_loss >= val_loss:
                best_val_loss = val_loss
            train_acc = test(model, train_loader)  # Assuming test is a predefined function
            test_acc = test(model, test_loader)
            test_exp_acc = test(model, test_exp_loader)
            test_lrn_acc = test(model, test_lrn_loader)
            tr_accuracies[epoch, i] = train_acc
            tst_accuracies[epoch, i] = test_acc
            tst_exp_accuracies[epoch, i] = test_exp_acc
            tst_lrn_accuracies[epoch, i] = test_lrn_acc

            print('Epoch: {:03d}, LR: {:7f}, Train Loss: {:.7f}, Val Loss: {:.7f}, Test Acc: {:.7f}, Exp Acc: {:.7f}, Lrn Acc: {:.7f}, Train Acc: {:.7f}'.format(epoch + 1, lr, train_loss, val_loss, test_acc, test_exp_acc, test_lrn_acc, train_acc))
        acc.append(test_acc)
        tr_acc.append(train_acc)

    return tr_accuracies, tst_accuracies, tst_exp_accuracies, tst_lrn_accuracies, acc, tr_acc


In [ ]:
import pickle as pkl

# RNI NORMAL INITIALIZATION

In [ ]:
RNI_10 = RNInit(random_dims = 10)
RNI_30 = RNInit(random_dims = 30)
RNI_62 = RNInit(random_dims = 62)

###rGCN results

In [ ]:
RGCN_N_results = {}

In [ ]:
rGCN_10N = rGCN(rni = RNI_10).to(device)
RGCN_N_results[10] = train_model(rGCN_10N)


/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7579038, Val Loss: 0.6972183, Test Acc: 0.5333333, Exp Acc: 0.5277778, Lrn Acc: 0.4907407, Train Acc: 0.5046296
Epoch: 002, LR: 0.001000, Train Loss: 0.7246856, Val Loss: 0.7045569, Test Acc: 0.5000000, Exp Acc: 0.4925926, Lrn Acc: 0.5018519, Train Acc: 0.5018519
Epoch: 003, LR: 0.001000, Train Loss: 0.7035161, Val Loss: 0.6953641, Test Acc: 0.4500000, Exp Acc: 0.5240741, Lrn Acc: 0.5185185, Train Acc: 0.5120370
Epoch: 004, LR: 0.001000, Train Loss: 0.7008863, Val Loss: 0.6938349, Test Acc: 0.5333333, Exp Acc: 0.5240741, Lrn Acc: 0.5222222, Train Acc: 0.5101852
Epoch: 005, LR: 0.001000, Train Loss: 0.7023275, Val Loss: 0.7025143, Test Acc: 0.5000000, Exp Acc: 0.4981481, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.001000, Train Loss: 0.7073240, Val Loss: 0.6957163, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.4981481, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.694456

In [ ]:
rGCN_30N = rGCN(rni = RNI_30).to(device)
RGCN_N_results[30] = train_model(rGCN_30N)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7555385, Val Loss: 0.6990669, Test Acc: 0.4916667, Exp Acc: 0.4962963, Lrn Acc: 0.5000000, Train Acc: 0.5037037
Epoch: 002, LR: 0.001000, Train Loss: 0.7011561, Val Loss: 0.7051253, Test Acc: 0.5083333, Exp Acc: 0.5037037, Lrn Acc: 0.5000000, Train Acc: 0.5027778
Epoch: 003, LR: 0.001000, Train Loss: 0.7088553, Val Loss: 0.6966444, Test Acc: 0.4916667, Exp Acc: 0.5055556, Lrn Acc: 0.5055556, Train Acc: 0.5037037
Epoch: 004, LR: 0.001000, Train Loss: 0.6983635, Val Loss: 0.7060369, Test Acc: 0.4916667, Exp Acc: 0.4981481, Lrn Acc: 0.5000000, Train Acc: 0.5009259
Epoch: 005, LR: 0.001000, Train Loss: 0.6990499, Val Loss: 0.6896902, Test Acc: 0.5166667, Exp Acc: 0.5462963, Lrn Acc: 0.5814815, Train Acc: 0.5305556
Epoch: 006, LR: 0.001000, Train Loss: 0.6979217, Val Loss: 0.6848325, Test Acc: 0.5833333, Exp Acc: 0.5462963, Lrn Acc: 0.5444444, Train Acc: 0.5361111
Epoch: 007, LR: 0.001000, Train Loss: 0.698139

In [ ]:
rGCN_62N = rGCN(rni = RNI_62).to(device)
RGCN_N_results[62] = train_model(rGCN_62N)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7621555, Val Loss: 0.7008982, Test Acc: 0.4750000, Exp Acc: 0.5240741, Lrn Acc: 0.5203704, Train Acc: 0.5416667
Epoch: 002, LR: 0.001000, Train Loss: 0.7194539, Val Loss: 0.7018045, Test Acc: 0.5000000, Exp Acc: 0.4981481, Lrn Acc: 0.5055556, Train Acc: 0.4972222
Epoch: 003, LR: 0.001000, Train Loss: 0.7013175, Val Loss: 0.6962954, Test Acc: 0.5166667, Exp Acc: 0.4981481, Lrn Acc: 0.5018519, Train Acc: 0.4962963
Epoch: 004, LR: 0.001000, Train Loss: 0.7068566, Val Loss: 0.7112265, Test Acc: 0.5083333, Exp Acc: 0.5055556, Lrn Acc: 0.5000000, Train Acc: 0.5064815
Epoch: 005, LR: 0.001000, Train Loss: 0.7138654, Val Loss: 0.6962291, Test Acc: 0.4916667, Exp Acc: 0.5055556, Lrn Acc: 0.5018519, Train Acc: 0.4990741
Epoch: 006, LR: 0.001000, Train Loss: 0.6994843, Val Loss: 0.7061144, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.699238

In [ ]:
with open('RGCN_N_results.pkl', 'wb') as pickle_file:
    pkl.dump(RGCN_N_results, pickle_file)

###rGIN results

In [ ]:
rGIN_N_results = {}

In [ ]:
rGIN_10N = rGIN(rni = RNI_10).to(device)
rGIN_N_results[10] = train_model(rGIN_10N)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7080010, Val Loss: 0.6952232, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5037037, Train Acc: 0.4990741
Epoch: 002, LR: 0.001000, Train Loss: 0.7028985, Val Loss: 0.6942450, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 0.6960771, Val Loss: 0.6940934, Test Acc: 0.4916667, Exp Acc: 0.4981481, Lrn Acc: 0.4962963, Train Acc: 0.4990741
Epoch: 004, LR: 0.001000, Train Loss: 0.6983170, Val Loss: 0.6927026, Test Acc: 0.4916667, Exp Acc: 0.5148148, Lrn Acc: 0.4833333, Train Acc: 0.4879630
Epoch: 005, LR: 0.001000, Train Loss: 0.6991464, Val Loss: 0.6927732, Test Acc: 0.4916667, Exp Acc: 0.4962963, Lrn Acc: 0.5018519, Train Acc: 0.4842593
Epoch: 006, LR: 0.001000, Train Loss: 0.6988809, Val Loss: 0.6938236, Test Acc: 0.4750000, Exp Acc: 0.4759259, Lrn Acc: 0.5055556, Train Acc: 0.4953704
Epoch: 007, LR: 0.001000, Train Loss: 0.695650

In [ ]:
rGIN_30N = rGIN(rni = RNI_30).to(device)
rGIN_N_results[30] = train_model(rGIN_30N)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7200159, Val Loss: 0.6963612, Test Acc: 0.5083333, Exp Acc: 0.5074074, Lrn Acc: 0.4925926, Train Acc: 0.5120370
Epoch: 002, LR: 0.001000, Train Loss: 0.7018835, Val Loss: 0.6955219, Test Acc: 0.5000000, Exp Acc: 0.4740741, Lrn Acc: 0.4870370, Train Acc: 0.4953704
Epoch: 003, LR: 0.001000, Train Loss: 0.6990820, Val Loss: 0.6944835, Test Acc: 0.4916667, Exp Acc: 0.5037037, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 004, LR: 0.001000, Train Loss: 0.6921017, Val Loss: 0.6929221, Test Acc: 0.5166667, Exp Acc: 0.4944444, Lrn Acc: 0.4944444, Train Acc: 0.4925926
Epoch: 005, LR: 0.001000, Train Loss: 0.7056962, Val Loss: 0.6944541, Test Acc: 0.5250000, Exp Acc: 0.5018519, Lrn Acc: 0.5018519, Train Acc: 0.5055556
Epoch: 006, LR: 0.001000, Train Loss: 0.6970144, Val Loss: 0.6954406, Test Acc: 0.5000000, Exp Acc: 0.5018519, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.693398

In [ ]:
rGIN_62N = rGIN(rni = RNI_62).to(device)
rGIN_N_results[62] = train_model(rGIN_62N)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7207253, Val Loss: 0.6944628, Test Acc: 0.5083333, Exp Acc: 0.5222222, Lrn Acc: 0.4851852, Train Acc: 0.5009259
Epoch: 002, LR: 0.001000, Train Loss: 0.7055045, Val Loss: 0.6931127, Test Acc: 0.5250000, Exp Acc: 0.4666667, Lrn Acc: 0.4944444, Train Acc: 0.4685185
Epoch: 003, LR: 0.001000, Train Loss: 0.6972375, Val Loss: 0.6938665, Test Acc: 0.5083333, Exp Acc: 0.5129630, Lrn Acc: 0.5074074, Train Acc: 0.4842593
Epoch: 004, LR: 0.001000, Train Loss: 0.7012959, Val Loss: 0.6936206, Test Acc: 0.4833333, Exp Acc: 0.4851852, Lrn Acc: 0.5203704, Train Acc: 0.4944444
Epoch: 005, LR: 0.001000, Train Loss: 0.6949497, Val Loss: 0.6935821, Test Acc: 0.5083333, Exp Acc: 0.4925926, Lrn Acc: 0.4981481, Train Acc: 0.4972222
Epoch: 006, LR: 0.001000, Train Loss: 0.7031844, Val Loss: 0.6935489, Test Acc: 0.4666667, Exp Acc: 0.4925926, Lrn Acc: 0.5259259, Train Acc: 0.4888889
Epoch: 007, LR: 0.001000, Train Loss: 0.694322

In [ ]:
with open('rGIN_N_results.pkl', 'wb') as pickle_file:
    pkl.dump(rGIN_N_results, pickle_file)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-41-89e5201b6772>", line 1, in <cell line: 1>
    with open('rGIN_N_results.pkl', 'wb') as pickle_file:
OSError: [Errno 107] Transport endpoint is not connected: 'rGIN_N_results.pkl'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2099, in showtraceback
    stb = value._render_traceback_()
AttributeError: 'OSError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/ultratb.py", line 1101, in get_records
    return _fixed_getinnerframes(etb, number_of_lines_of_context, tb_of

In [ ]:
rGIN_N_ELU_results = {}

In [ ]:
rGIN_10N = rGIN(rni = RNI_10).to(device)
rGIN_N_ELU_results[10] = train_model(rGIN_10N)


/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 010, LR: 0.001000, Train Loss: 0.6968477, Val Loss: 0.6953881, Test Acc: 0.5000000, Exp Acc: 0.5055556, Lrn Acc: 0.5000000, Train Acc: 0.5009259
Epoch: 020, LR: 0.001000, Train Loss: 0.6932480, Val Loss: 0.6866628, Test Acc: 0.5750000, Exp Acc: 0.5407407, Lrn Acc: 0.5407407, Train Acc: 0.5648148
Epoch: 030, LR: 0.001000, Train Loss: 0.6963190, Val Loss: 0.6923314, Test Acc: 0.5000000, Exp Acc: 0.5166667, Lrn Acc: 0.5148148, Train Acc: 0.5046296
Epoch: 040, LR: 0.001000, Train Loss: 0.6973588, Val Loss: 0.6928052, Test Acc: 0.5500000, Exp Acc: 0.5259259, Lrn Acc: 0.5203704, Train Acc: 0.5305556
Epoch: 050, LR: 0.001000, Train Loss: 0.6858708, Val Loss: 0.6795227, Test Acc: 0.5416667, Exp Acc: 0.5870370, Lrn Acc: 0.5666667, Train Acc: 0.5351852
Epoch: 060, LR: 0.001000, Train Loss: 0.6717378, Val Loss: 0.6728516, Test Acc: 0.6583333, Exp Acc: 0.6425926, Lrn Acc: 0.6222222, Train Acc: 0.5990741
Epoch: 070, LR: 0.001000, Train Loss: 0.590366

In [ ]:
rGIN_10N = rGIN(rni = RNI_10).to(device)
rGIN_N_ELU_results[10] = train_model(rGIN_10N, splits = 2)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7197532, Val Loss: 0.6942854, Test Acc: 0.5033333, Exp Acc: 0.4933333, Lrn Acc: 0.5066667, Train Acc: 0.5033333
Epoch: 002, LR: 0.001000, Train Loss: 0.7012920, Val Loss: 0.7057839, Test Acc: 0.4816667, Exp Acc: 0.4800000, Lrn Acc: 0.4966667, Train Acc: 0.5116667
Epoch: 003, LR: 0.001000, Train Loss: 0.6948277, Val Loss: 0.6980808, Test Acc: 0.5433333, Exp Acc: 0.5333333, Lrn Acc: 0.5000000, Train Acc: 0.4933333
Epoch: 004, LR: 0.001000, Train Loss: 0.7038856, Val Loss: 0.6964138, Test Acc: 0.4750000, Exp Acc: 0.4533333, Lrn Acc: 0.5133333, Train Acc: 0.5283333
Epoch: 005, LR: 0.001000, Train Loss: 0.6973551, Val Loss: 0.6910689, Test Acc: 0.4666667, Exp Acc: 0.5166667, Lrn Acc: 0.5100000, Train Acc: 0.5483333
Epoch: 006, LR: 0.001000, Train Loss: 0.6984882, Val Loss: 0.6940414, Test Acc: 0.4950000, Exp Acc: 0.5066667, Lrn Acc: 0.4966667, Train Acc: 0.4783333
Epoch: 007, LR: 0.001000, Train Loss: 0.692654

NameError: ignored

In [ ]:
rGIN_10N = rGIN(rni = RNI_30).to(device)
rGIN_N_ELU_results[10] = train_model(rGIN_30N, splits = 2)

In [ ]:
rGIN_30N = rGIN(rni = RNI_30).to(device)
rGIN_N_ELU_results[30] = train_model(rGIN_30N)

---------------- Split 0 ----------------
Epoch: 010, LR: 0.001000, Train Loss: 0.6915379, Val Loss: 0.6904660, Test Acc: 0.5250000, Exp Acc: 0.5259259, Lrn Acc: 0.5462963, Train Acc: 0.5268519
Epoch: 020, LR: 0.001000, Train Loss: 0.6972599, Val Loss: 0.6913441, Test Acc: 0.5250000, Exp Acc: 0.5148148, Lrn Acc: 0.5092593, Train Acc: 0.5129630
Epoch: 030, LR: 0.001000, Train Loss: 0.6921218, Val Loss: 0.6923905, Test Acc: 0.5250000, Exp Acc: 0.5462963, Lrn Acc: 0.5240741, Train Acc: 0.5277778
Epoch: 040, LR: 0.001000, Train Loss: 0.6920446, Val Loss: 0.6788684, Test Acc: 0.5000000, Exp Acc: 0.5425926, Lrn Acc: 0.5537037, Train Acc: 0.5685185
Epoch: 050, LR: 0.001000, Train Loss: 0.6814741, Val Loss: 0.6680736, Test Acc: 0.6250000, Exp Acc: 0.5740741, Lrn Acc: 0.5703704, Train Acc: 0.5750000
Epoch: 060, LR: 0.001000, Train Loss: 0.6804129, Val Loss: 0.6529567, Test Acc: 0.5666667, Exp Acc: 0.6074074, Lrn Acc: 0.5666667, Train Acc: 0.6166667
Epoch: 070, LR: 0.001000, Train Loss: 0.557604

In [ ]:
rGIN_62N = rGIN(rni = RNI_62).to(device)
rGIN_N_ELU_results[62] = train_model(rGIN_62N)

---------------- Split 0 ----------------
Epoch: 010, LR: 0.001000, Train Loss: 0.6949209, Val Loss: 0.6980782, Test Acc: 0.5333333, Exp Acc: 0.5074074, Lrn Acc: 0.5000000, Train Acc: 0.5046296
Epoch: 020, LR: 0.001000, Train Loss: 0.6970788, Val Loss: 0.6927233, Test Acc: 0.5416667, Exp Acc: 0.5314815, Lrn Acc: 0.5314815, Train Acc: 0.5277778
Epoch: 030, LR: 0.001000, Train Loss: 0.6911904, Val Loss: 0.6924501, Test Acc: 0.6166667, Exp Acc: 0.5351852, Lrn Acc: 0.5370370, Train Acc: 0.5185185
Epoch: 040, LR: 0.001000, Train Loss: 0.6791985, Val Loss: 0.6775166, Test Acc: 0.6250000, Exp Acc: 0.5407407, Lrn Acc: 0.5851852, Train Acc: 0.5648148
Epoch: 050, LR: 0.001000, Train Loss: 0.6531595, Val Loss: 0.6435618, Test Acc: 0.6000000, Exp Acc: 0.6722222, Lrn Acc: 0.6333333, Train Acc: 0.6287037
Epoch: 060, LR: 0.001000, Train Loss: 0.6884974, Val Loss: 0.6830323, Test Acc: 0.6500000, Exp Acc: 0.5314815, Lrn Acc: 0.5685185, Train Acc: 0.5648148
Epoch: 070, LR: 0.001000, Train Loss: 0.567823

In [ ]:
with open('rGIN_N_ELU_results.pkl', 'wb') as pickle_file:
    pkl.dump(rGIN_N_ELU_results, pickle_file)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-24-cf498987aaee>", line 1, in <cell line: 1>
    with open('rGIN_N_ELU_results.pkl', 'wb') as pickle_file:
OSError: [Errno 107] Transport endpoint is not connected: 'rGIN_N_ELU_results.pkl'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2099, in showtraceback
    stb = value._render_traceback_()
AttributeError: 'OSError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/ultratb.py", line 1101, in get_records
    return _fixed_getinnerframes(etb, number_of_lines_of_contex

# RNI XAVIER NORMAL INITIALIZATION

In [ ]:
RNI_10 = RNInit(random_dims = 10, distribution = 'xn')
RNI_30 = RNInit(random_dims = 30, distribution = 'xn')
RNI_62 = RNInit(random_dims = 50, distribution = 'xn')

###rGCN results

In [ ]:
RGCN_XN_results = {}

In [ ]:
rGCN_10XN = rGCN(rni = RNI_10, pooling = 'sum').to(device)
RGCN_XN_results[10] = train_model(rGCN_10XN, splits = 2)


/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7260395, Val Loss: 0.6991135, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 002, LR: 0.001000, Train Loss: 0.7463579, Val Loss: 0.6940456, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 0.7099963, Val Loss: 0.6966124, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 004, LR: 0.001000, Train Loss: 0.7133061, Val Loss: 0.6942163, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.4966667, Train Acc: 0.5016667
Epoch: 005, LR: 0.001000, Train Loss: 0.7055883, Val Loss: 0.6934302, Test Acc: 0.5000000, Exp Acc: 0.4966667, Lrn Acc: 0.5033333, Train Acc: 0.5000000
Epoch: 006, LR: 0.001000, Train Loss: 0.7052228, Val Loss: 0.7041084, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.712314

KeyboardInterrupt: ignored

In [ ]:
rGCN_30XN = rGCN(rni = RNI_30).to(device)
RGCN_XN_results[30] = train_model(rGCN_30XN, splits = 2, learning_rate = 5*10e-4)

/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.005000, Train Loss: 0.8784554, Val Loss: 0.6933217, Test Acc: 0.4983333, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.4966667
Epoch: 002, LR: 0.005000, Train Loss: 0.7192396, Val Loss: 0.6941060, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.005000, Train Loss: 0.7076734, Val Loss: 0.6939253, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 004, LR: 0.005000, Train Loss: 0.7044060, Val Loss: 0.6957438, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 005, LR: 0.005000, Train Loss: 0.7013760, Val Loss: 0.6932685, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.005000, Train Loss: 0.6968496, Val Loss: 0.6949582, Test Acc: 0.5016667, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.005000, Train Loss: 0.700914

KeyboardInterrupt: ignored

In [ ]:
rGCN_62XN = rGCN(rni = RNI_62, num_layers = 10).to(device)
RGCN_XN_results[62] = train_model(rGCN_62XN, learning_rate = 5*10e-4, splits = 2, batch_size = 40)

/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.005000, Train Loss: 1.0794937, Val Loss: 0.7690226, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 002, LR: 0.005000, Train Loss: 0.7857066, Val Loss: 0.7657019, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.005000, Train Loss: 0.7106889, Val Loss: 0.7146129, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 004, LR: 0.005000, Train Loss: 0.7047637, Val Loss: 0.6934659, Test Acc: 0.4916667, Exp Acc: 0.5000000, Lrn Acc: 0.5033333, Train Acc: 0.5016667
Epoch: 005, LR: 0.005000, Train Loss: 0.6996606, Val Loss: 0.6956647, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.005000, Train Loss: 0.7073768, Val Loss: 0.6935435, Test Acc: 0.4950000, Exp Acc: 0.4966667, Lrn Acc: 0.4933333, Train Acc: 0.5000000
Epoch: 007, LR: 0.005000, Train Loss: 0.708651

KeyboardInterrupt: ignored

In [ ]:
import pickle as pkl

In [ ]:
with open('RGCN_XN_results.pkl', 'wb') as pickle_file:
    pkl.dump(RGCN_XN_results, pickle_file)

NameError: ignored

###rGIN results

In [ ]:
rGIN_XN_results = {}

In [ ]:
rGIN_10XN = rGIN(rni = RNI_10).to(device)
rGIN_XN_results[10] = train_model(rGIN_10XN)


---------------- Split 0 ----------------
Epoch: 010, LR: 0.001000, Train Loss: 0.6893074, Val Loss: 0.6785666, Test Acc: 0.5250000, Exp Acc: 0.5648148, Lrn Acc: 0.6055556, Train Acc: 0.5500000
Epoch: 020, LR: 0.001000, Train Loss: 0.6197236, Val Loss: 0.6541670, Test Acc: 0.6166667, Exp Acc: 0.6277778, Lrn Acc: 0.6166667, Train Acc: 0.6120370
Epoch: 030, LR: 0.001000, Train Loss: 0.6155634, Val Loss: 0.6150807, Test Acc: 0.6500000, Exp Acc: 0.6722222, Lrn Acc: 0.7055556, Train Acc: 0.6944444
Epoch: 040, LR: 0.001000, Train Loss: 0.5115763, Val Loss: 0.6706480, Test Acc: 0.6500000, Exp Acc: 0.6518519, Lrn Acc: 0.6814815, Train Acc: 0.6398148
Epoch: 050, LR: 0.001000, Train Loss: 0.4485839, Val Loss: 0.4718000, Test Acc: 0.6916667, Exp Acc: 0.7111111, Lrn Acc: 0.7203704, Train Acc: 0.7250000
Epoch: 060, LR: 0.001000, Train Loss: 0.3667459, Val Loss: 0.3104159, Test Acc: 0.8833333, Exp Acc: 0.7851852, Lrn Acc: 0.8166667, Train Acc: 0.8240741
Epoch: 070, LR: 0.001000, Train Loss: 0.337192

In [ ]:
rGIN_30XN = rGIN(rni = RNI_30).to(device)
rGIN_XN_results[30] = train_model(rGIN_30XN)

---------------- Split 0 ----------------
Epoch: 010, LR: 0.001000, Train Loss: 0.6948041, Val Loss: 0.6918233, Test Acc: 0.5250000, Exp Acc: 0.5222222, Lrn Acc: 0.5203704, Train Acc: 0.5231481
Epoch: 020, LR: 0.001000, Train Loss: 0.6916032, Val Loss: 0.6916067, Test Acc: 0.5666667, Exp Acc: 0.5759259, Lrn Acc: 0.5314815, Train Acc: 0.5296296
Epoch: 030, LR: 0.001000, Train Loss: 0.6888068, Val Loss: 0.6853243, Test Acc: 0.5666667, Exp Acc: 0.5944444, Lrn Acc: 0.5944444, Train Acc: 0.5851852
Epoch: 040, LR: 0.001000, Train Loss: 0.5935058, Val Loss: 0.6391355, Test Acc: 0.6166667, Exp Acc: 0.6611111, Lrn Acc: 0.6555556, Train Acc: 0.6055556
Epoch: 050, LR: 0.001000, Train Loss: 0.5018226, Val Loss: 0.6443393, Test Acc: 0.7000000, Exp Acc: 0.6555556, Lrn Acc: 0.6574074, Train Acc: 0.6657407
Epoch: 060, LR: 0.001000, Train Loss: 0.4269067, Val Loss: 0.4003745, Test Acc: 0.8083333, Exp Acc: 0.7574074, Lrn Acc: 0.8166667, Train Acc: 0.8064815
Epoch: 070, LR: 0.001000, Train Loss: 0.343440

In [ ]:
rGIN_62XN = rGIN(rni = RNI_62).to(device)
rGIN_XN_results[62] = train_model(rGIN_62XN)

---------------- Split 0 ----------------
Epoch: 010, LR: 0.001000, Train Loss: 0.6944188, Val Loss: 0.6943083, Test Acc: 0.5000000, Exp Acc: 0.5185185, Lrn Acc: 0.5277778, Train Acc: 0.5222222
Epoch: 020, LR: 0.001000, Train Loss: 0.6953365, Val Loss: 0.6922150, Test Acc: 0.5333333, Exp Acc: 0.5259259, Lrn Acc: 0.5129630, Train Acc: 0.5287037
Epoch: 030, LR: 0.001000, Train Loss: 0.6724888, Val Loss: 0.6773393, Test Acc: 0.5750000, Exp Acc: 0.5833333, Lrn Acc: 0.5870370, Train Acc: 0.6000000
Epoch: 040, LR: 0.001000, Train Loss: 0.5752326, Val Loss: 0.5966766, Test Acc: 0.6916667, Exp Acc: 0.6555556, Lrn Acc: 0.7055556, Train Acc: 0.7268519
Epoch: 050, LR: 0.001000, Train Loss: 0.4735818, Val Loss: 0.4571060, Test Acc: 0.7083333, Exp Acc: 0.7481481, Lrn Acc: 0.7722222, Train Acc: 0.7537037
Epoch: 060, LR: 0.001000, Train Loss: 0.4412589, Val Loss: 0.4259844, Test Acc: 0.7750000, Exp Acc: 0.7648148, Lrn Acc: 0.7407407, Train Acc: 0.7870370
Epoch: 070, LR: 0.001000, Train Loss: 0.310453

In [ ]:
rGIN_XN_results

NameError: ignored

In [ ]:
with open('rGIN_XN_results.pkl', 'wb') as pickle_file:
    pkl.dump(rGIN_XN_results, pickle_file)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-33-771296b9f493>", line 1, in <cell line: 1>
    with open('rGIN_XN_results.pkl', 'wb') as pickle_file:
OSError: [Errno 107] Transport endpoint is not connected: 'rGIN_XN_results.pkl'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2099, in showtraceback
    stb = value._render_traceback_()
AttributeError: 'OSError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/ultratb.py", line 1101, in get_records
    return _fixed_getinnerframes(etb, number_of_lines_of_context, tb_

# RNI XAVIER UNIFORM INITIALIZATION

In [ ]:
RNI_10 = RNInit(random_dims = 10, distribution = 'xu')
RNI_30 = RNInit(random_dims = 30, distribution = 'xu')
RNI_62 = RNInit(random_dims = 50, distribution = 'xu')

###rGCN results

In [ ]:
RGCN_XU_results = {}

In [ ]:
rGCN_10XU = rGCN(rni = RNI_10).to(device)
RGCN_XU_results[10] = train_model(rGCN_10XU)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7399645, Val Loss: 0.6950304, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 002, LR: 0.001000, Train Loss: 0.7102141, Val Loss: 0.6971179, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 0.7059604, Val Loss: 0.6936643, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5037037, Train Acc: 0.5027778
Epoch: 004, LR: 0.001000, Train Loss: 0.6959019, Val Loss: 0.6977934, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 005, LR: 0.001000, Train Loss: 0.7000870, Val Loss: 0.6936749, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.001000, Train Loss: 0.7035451, Val Loss: 0.6950020, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.696556

KeyboardInterrupt: ignored

In [ ]:
rGCN_30XU = rGCN(rni = RNI_30).to(device)
RGCN_XU_results[30] = train_model(rGCN_30XU)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7772775, Val Loss: 0.7693685, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 002, LR: 0.001000, Train Loss: 0.7167284, Val Loss: 0.6960212, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5055556, Train Acc: 0.4972222
Epoch: 003, LR: 0.001000, Train Loss: 0.7093066, Val Loss: 0.6974745, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000


ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-61-126000ab523f>", line 2, in <cell line: 2>
    RGCN_XU_results[30] = train_model(rGCN_30XU)
  File "<ipython-input-25-ff8b9f561f6a>", line 49, in train_model
    test_acc = test(model, test_loader)
  File "<ipython-input-16-7c2debb5d22a>", line 47, in test
    pred = model(data).max(1)[1]
  File "/usr/local/lib/python3.10/dist-packages/torch/nn/modules/module.py", line 1518, in _wrapped_call_impl
    return self._call_impl(*args, **kwargs)
  File "/usr/local/lib/python3.10/dist-packages/torch/nn/modules/module.py", line 1527, in _call_impl
    return forward_call(*args, **kwargs)
  File "<ipython-input-12-262d34d7cca8>", line 30, in forward
    x = self.activation(layer(x, data.edge_index))
  File "/usr/local/lib/python3.10/dist-packages/torch/nn/modules/module.py", lin

In [ ]:
rGCN_62XU = rGCN(rni = RNI_62).to(device)
RGCN_XU_results[62] = train_model(rGCN_62XU)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7466683, Val Loss: 0.6932315, Test Acc: 0.4833333, Exp Acc: 0.5018519, Lrn Acc: 0.5037037, Train Acc: 0.5046296
Epoch: 002, LR: 0.001000, Train Loss: 0.7033232, Val Loss: 0.6990094, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 0.7115059, Val Loss: 0.6940605, Test Acc: 0.5083333, Exp Acc: 0.5055556, Lrn Acc: 0.5000000, Train Acc: 0.5009259
Epoch: 004, LR: 0.001000, Train Loss: 0.7014041, Val Loss: 0.6932058, Test Acc: 0.5166667, Exp Acc: 0.5000000, Lrn Acc: 0.5018519, Train Acc: 0.4981481
Epoch: 005, LR: 0.001000, Train Loss: 0.6968961, Val Loss: 0.6968893, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.001000, Train Loss: 0.7007353, Val Loss: 0.6969971, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.699582

KeyboardInterrupt: ignored

In [ ]:
with open('RGCN_XU_results.pkl', 'wb') as pickle_file:
    pkl.dump(RGCN_XU_results, pickle_file)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-62-bbfd37c1690b>", line 1, in <cell line: 1>
    with open('RGCN_XU_results.pkl', 'wb') as pickle_file:
OSError: [Errno 107] Transport endpoint is not connected: 'RGCN_XU_results.pkl'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2099, in showtraceback
    stb = value._render_traceback_()
AttributeError: 'OSError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/ultratb.py", line 1101, in get_records
    return _fixed_getinnerframes(etb, number_of_lines_of_context, tb_

###rGIN results

In [ ]:
rGIN_XU_results = {}

In [ ]:
rGIN_10XU = rGIN(rni = RNI_10).to(device)
rGIN_XU_results[10] = train_model(rGIN_10XU)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7039873, Val Loss: 0.7114639, Test Acc: 0.5083333, Exp Acc: 0.4962963, Lrn Acc: 0.4981481, Train Acc: 0.4907407
Epoch: 002, LR: 0.001000, Train Loss: 0.7015268, Val Loss: 0.6947625, Test Acc: 0.4833333, Exp Acc: 0.5000000, Lrn Acc: 0.4981481, Train Acc: 0.4990741
Epoch: 003, LR: 0.001000, Train Loss: 0.6998474, Val Loss: 0.6941257, Test Acc: 0.5000000, Exp Acc: 0.4981481, Lrn Acc: 0.5037037, Train Acc: 0.5055556
Epoch: 004, LR: 0.001000, Train Loss: 0.6980932, Val Loss: 0.6901602, Test Acc: 0.5250000, Exp Acc: 0.5148148, Lrn Acc: 0.5277778, Train Acc: 0.5009259
Epoch: 005, LR: 0.001000, Train Loss: 0.6985852, Val Loss: 0.7012863, Test Acc: 0.5250000, Exp Acc: 0.5018519, Lrn Acc: 0.4981481, Train Acc: 0.4953704
Epoch: 006, LR: 0.001000, Train Loss: 0.6934898, Val Loss: 0.6964820, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.697196

In [ ]:
rGIN_30XU = rGIN(rni = RNI_30).to(device)
rGIN_XU_results[30] = train_model(rGIN_30XU)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7127801, Val Loss: 0.6971672, Test Acc: 0.5333333, Exp Acc: 0.5111111, Lrn Acc: 0.5074074, Train Acc: 0.5046296
Epoch: 002, LR: 0.001000, Train Loss: 0.7027559, Val Loss: 0.7155552, Test Acc: 0.5000000, Exp Acc: 0.5018519, Lrn Acc: 0.4962963, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 0.7010859, Val Loss: 0.6962465, Test Acc: 0.5000000, Exp Acc: 0.5111111, Lrn Acc: 0.4925926, Train Acc: 0.5175926
Epoch: 004, LR: 0.001000, Train Loss: 0.6997281, Val Loss: 0.6931170, Test Acc: 0.5250000, Exp Acc: 0.5055556, Lrn Acc: 0.5000000, Train Acc: 0.5101852
Epoch: 005, LR: 0.001000, Train Loss: 0.6943603, Val Loss: 0.6989411, Test Acc: 0.5333333, Exp Acc: 0.4981481, Lrn Acc: 0.4888889, Train Acc: 0.5129630
Epoch: 006, LR: 0.001000, Train Loss: 0.7002485, Val Loss: 0.7042907, Test Acc: 0.5250000, Exp Acc: 0.5129630, Lrn Acc: 0.5185185, Train Acc: 0.5027778
Epoch: 007, LR: 0.001000, Train Loss: 0.697542

In [ ]:
rGIN_62XU = rGIN(rni = RNI_62).to(device)
rGIN_XU_results[62] = train_model(rGIN_62XU)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7097706, Val Loss: 0.6957885, Test Acc: 0.5250000, Exp Acc: 0.5166667, Lrn Acc: 0.4944444, Train Acc: 0.5277778
Epoch: 002, LR: 0.001000, Train Loss: 0.6951003, Val Loss: 0.7073995, Test Acc: 0.4666667, Exp Acc: 0.5185185, Lrn Acc: 0.5314815, Train Acc: 0.5453704
Epoch: 003, LR: 0.001000, Train Loss: 0.6965852, Val Loss: 0.6959236, Test Acc: 0.4916667, Exp Acc: 0.5259259, Lrn Acc: 0.5148148, Train Acc: 0.5268519
Epoch: 004, LR: 0.001000, Train Loss: 0.7008013, Val Loss: 0.6943354, Test Acc: 0.5000000, Exp Acc: 0.5388889, Lrn Acc: 0.5388889, Train Acc: 0.5138889
Epoch: 005, LR: 0.001000, Train Loss: 0.7001750, Val Loss: 0.6967795, Test Acc: 0.5083333, Exp Acc: 0.5259259, Lrn Acc: 0.5425926, Train Acc: 0.5296296
Epoch: 006, LR: 0.001000, Train Loss: 0.6988873, Val Loss: 0.6939684, Test Acc: 0.5500000, Exp Acc: 0.4777778, Lrn Acc: 0.4944444, Train Acc: 0.4981481
Epoch: 007, LR: 0.001000, Train Loss: 0.693549

In [ ]:
with open('rGIN_XU_results.pkl', 'wb') as pickle_file:
    pkl.dump(rGIN_XU_results, pickle_file)

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-65-af879e67271f>", line 1, in <cell line: 1>
    with open('rGIN_XU_results.pkl', 'wb') as pickle_file:
OSError: [Errno 107] Transport endpoint is not connected: 'rGIN_XU_results.pkl'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2099, in showtraceback
    stb = value._render_traceback_()
AttributeError: 'OSError' object has no attribute '_render_traceback_'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/ultratb.py", line 1101, in get_records
    return _fixed_getinnerframes(etb, number_of_lines_of_context, tb_

# RNI UNIFORM INITIALIZATION

In [ ]:
RNI_10 = RNInit(random_dims = 10, distribution = 'u')
RNI_30 = RNInit(random_dims = 30, distribution = 'u')
RNI_62 = RNInit(random_dims = 50, distribution = 'u')

###rGCN results

In [ ]:
RGCN_U_results = {}

In [ ]:
rGCN_10U = rGCN(rni = RNI_10).to(device)
RGCN_U_results[10] = train_model(rGCN_10U)


---------------- Split 0 ----------------
Epoch: 005, LR: 0.001000, Train Loss: 0.7007995, Val Loss: 0.6953604, Test Acc: 0.5166667, Exp Acc: 0.4962963, Lrn Acc: 0.5425926, Train Acc: 0.4888889
Epoch: 010, LR: 0.001000, Train Loss: 0.7016888, Val Loss: 0.7000618, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 015, LR: 0.001000, Train Loss: 0.6997226, Val Loss: 0.6935494, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5018519, Train Acc: 0.5000000
Epoch: 020, LR: 0.001000, Train Loss: 0.6862435, Val Loss: 0.6712247, Test Acc: 0.6833333, Exp Acc: 0.6240741, Lrn Acc: 0.5888889, Train Acc: 0.6120370
Epoch: 025, LR: 0.001000, Train Loss: 0.6861960, Val Loss: 0.6880150, Test Acc: 0.5166667, Exp Acc: 0.5148148, Lrn Acc: 0.5111111, Train Acc: 0.5120370
Epoch: 030, LR: 0.001000, Train Loss: 0.5619702, Val Loss: 0.4725520, Test Acc: 0.7416667, Exp Acc: 0.7777778, Lrn Acc: 0.7407407, Train Acc: 0.7824074
Epoch: 035, LR: 0.001000, Train Loss: 0.441275

In [ ]:
rGCN_30U = rGCN(rni = RNI_30).to(device)
RGCN_U_results[30] = train_model(rGCN_30U)

---------------- Split 0 ----------------
Epoch: 005, LR: 0.001000, Train Loss: 0.7027768, Val Loss: 0.6882623, Test Acc: 0.5583333, Exp Acc: 0.5444444, Lrn Acc: 0.5370370, Train Acc: 0.5361111
Epoch: 010, LR: 0.001000, Train Loss: 0.6949752, Val Loss: 0.6888333, Test Acc: 0.5166667, Exp Acc: 0.5796296, Lrn Acc: 0.5962963, Train Acc: 0.5472222
Epoch: 015, LR: 0.001000, Train Loss: 0.6934044, Val Loss: 0.6784883, Test Acc: 0.6500000, Exp Acc: 0.5555556, Lrn Acc: 0.5574074, Train Acc: 0.5712963
Epoch: 020, LR: 0.001000, Train Loss: 0.6577471, Val Loss: 0.6308766, Test Acc: 0.6416667, Exp Acc: 0.7425926, Lrn Acc: 0.6703704, Train Acc: 0.6944444
Epoch: 025, LR: 0.001000, Train Loss: 0.5102010, Val Loss: 0.4234134, Test Acc: 0.8333333, Exp Acc: 0.8111111, Lrn Acc: 0.7592593, Train Acc: 0.7805556
Epoch: 030, LR: 0.001000, Train Loss: 0.3870544, Val Loss: 0.3476480, Test Acc: 0.8583333, Exp Acc: 0.8370370, Lrn Acc: 0.8296296, Train Acc: 0.8398148
Epoch: 035, LR: 0.001000, Train Loss: 0.281600

In [ ]:
rGCN_62U = rGCN(rni = RNI_62).to(device)
RGCN_U_results[62] = train_model(rGCN_62U)

---------------- Split 0 ----------------
Epoch: 005, LR: 0.001000, Train Loss: 0.6993037, Val Loss: 0.6982403, Test Acc: 0.4833333, Exp Acc: 0.5203704, Lrn Acc: 0.5370370, Train Acc: 0.5046296
Epoch: 010, LR: 0.001000, Train Loss: 0.7000213, Val Loss: 0.6975816, Test Acc: 0.5166667, Exp Acc: 0.5055556, Lrn Acc: 0.5000000, Train Acc: 0.5009259
Epoch: 015, LR: 0.001000, Train Loss: 0.6878092, Val Loss: 0.6869000, Test Acc: 0.5166667, Exp Acc: 0.5129630, Lrn Acc: 0.5203704, Train Acc: 0.5296296
Epoch: 020, LR: 0.001000, Train Loss: 0.6880431, Val Loss: 0.6740970, Test Acc: 0.5666667, Exp Acc: 0.6185185, Lrn Acc: 0.6129630, Train Acc: 0.6055556
Epoch: 025, LR: 0.001000, Train Loss: 0.5830444, Val Loss: 0.5653365, Test Acc: 0.7166667, Exp Acc: 0.7203704, Lrn Acc: 0.6796296, Train Acc: 0.7009259
Epoch: 030, LR: 0.001000, Train Loss: 0.4442381, Val Loss: 0.4601903, Test Acc: 0.7583333, Exp Acc: 0.8055556, Lrn Acc: 0.7796296, Train Acc: 0.7675926
Epoch: 035, LR: 0.001000, Train Loss: 0.352984

In [ ]:
with open('RGCN_U_results.pkl', 'wb') as pickle_file:
    pkl.dump(RGCN_U_results, pickle_file)

###rGIN results

In [ ]:
rGIN_U_results = {}

In [ ]:
rGIN_10U = rGIN(rni = RNI_10).to(device)
rGIN_U_results[10] = train_model(rGIN_10U, epochs = 300)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7112377, Val Loss: 0.7039333, Test Acc: 0.5166667, Exp Acc: 0.5037037, Lrn Acc: 0.4833333, Train Acc: 0.5018519
Epoch: 002, LR: 0.001000, Train Loss: 0.7010474, Val Loss: 0.6950698, Test Acc: 0.4916667, Exp Acc: 0.5000000, Lrn Acc: 0.5240741, Train Acc: 0.5083333
Epoch: 003, LR: 0.001000, Train Loss: 0.7004917, Val Loss: 0.6998631, Test Acc: 0.5500000, Exp Acc: 0.5018519, Lrn Acc: 0.4796296, Train Acc: 0.4916667
Epoch: 004, LR: 0.001000, Train Loss: 0.6986511, Val Loss: 0.6914704, Test Acc: 0.5833333, Exp Acc: 0.4944444, Lrn Acc: 0.5092593, Train Acc: 0.4962963
Epoch: 005, LR: 0.001000, Train Loss: 0.6952128, Val Loss: 0.6945756, Test Acc: 0.5166667, Exp Acc: 0.5148148, Lrn Acc: 0.4888889, Train Acc: 0.5166667
Epoch: 006, LR: 0.001000, Train Loss: 0.6965324, Val Loss: 0.6961405, Test Acc: 0.4750000, Exp Acc: 0.5129630, Lrn Acc: 0.5055556, Train Acc: 0.5101852
Epoch: 007, LR: 0.001000, Train Loss: 0.695150

In [ ]:
rGIN_30U = rGIN(rni = RNI_30).to(device)
rGIN_U_results[30] = train_model(rGIN_30U)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7259268, Val Loss: 0.6933865, Test Acc: 0.5083333, Exp Acc: 0.4944444, Lrn Acc: 0.4944444, Train Acc: 0.5231481
Epoch: 002, LR: 0.001000, Train Loss: 0.7070475, Val Loss: 0.7081841, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 0.7026103, Val Loss: 0.6951477, Test Acc: 0.4916667, Exp Acc: 0.4611111, Lrn Acc: 0.5111111, Train Acc: 0.5175926
Epoch: 004, LR: 0.001000, Train Loss: 0.7056622, Val Loss: 0.6925856, Test Acc: 0.5083333, Exp Acc: 0.5018519, Lrn Acc: 0.4796296, Train Acc: 0.5212963
Epoch: 005, LR: 0.001000, Train Loss: 0.6971079, Val Loss: 0.6933165, Test Acc: 0.5500000, Exp Acc: 0.4962963, Lrn Acc: 0.5370370, Train Acc: 0.5148148
Epoch: 006, LR: 0.001000, Train Loss: 0.7001952, Val Loss: 0.6947324, Test Acc: 0.5166667, Exp Acc: 0.4962963, Lrn Acc: 0.5148148, Train Acc: 0.5175926
Epoch: 007, LR: 0.001000, Train Loss: 0.695966

In [ ]:
rGIN_62U = rGIN(rni = RNI_62).to(device)
rGIN_U_results[62] = train_model(rGIN_62U)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7153770, Val Loss: 0.6982836, Test Acc: 0.5000000, Exp Acc: 0.5074074, Lrn Acc: 0.5055556, Train Acc: 0.4907407
Epoch: 002, LR: 0.001000, Train Loss: 0.6995633, Val Loss: 0.7047018, Test Acc: 0.5083333, Exp Acc: 0.4962963, Lrn Acc: 0.4925926, Train Acc: 0.4990741
Epoch: 003, LR: 0.001000, Train Loss: 0.6992180, Val Loss: 0.6966634, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5018519, Train Acc: 0.4990741
Epoch: 004, LR: 0.001000, Train Loss: 0.6982921, Val Loss: 0.6964781, Test Acc: 0.5333333, Exp Acc: 0.4888889, Lrn Acc: 0.5129630, Train Acc: 0.5046296
Epoch: 005, LR: 0.001000, Train Loss: 0.6992492, Val Loss: 0.6945959, Test Acc: 0.5583333, Exp Acc: 0.4962963, Lrn Acc: 0.4925926, Train Acc: 0.5296296
Epoch: 006, LR: 0.001000, Train Loss: 0.6976854, Val Loss: 0.6916714, Test Acc: 0.4916667, Exp Acc: 0.5092593, Lrn Acc: 0.5000000, Train Acc: 0.5287037
Epoch: 007, LR: 0.001000, Train Loss: 0.697522

In [ ]:
import pickle as pkl

In [ ]:
with open('rGIN_U_results2.pkl', 'wb') as pickle_file:
    pkl.dump(rGIN_U_results, pickle_file)

#COGNN RESULTS

In [ ]:
RNI_U0 = RNInit(random_dims = 0, distribution = 'ones')
RNI_U5 = RNInit(random_dims = 5, distribution = 'ones')
RNI_U30 = RNInit(random_dims = 30, distribution = 'ones')

CoGNN_results = {}

In [ ]:
params_cognn_relu = {
    "dataset": None,
    "pool": Pool.SUM,
    "learn_temp": False,
    "temp_model_type": ModelType.LIN,
    "tau0": 0,
    "temp": 0.01,
    "max_epochs": 3000,
    "batch_size": 14,
    "lr": 1e-3,
    "dropout": 0,
    "env_model_type": ModelType.MEAN_GNN,
    "env_num_layers": 20,
    "env_dim": 64,
    "in_dim" : 2,
    'out_dim' : 2,
    "skip": False,
    "batch_norm": False,
    "layer_norm": False,
    "dec_num_layers": 1,
    "pos_enc": PosEncoder.NONE,
    "act_model_type": ModelType.MEAN_GNN,
    "act_num_layers": 1,
    "act_dim": 16,
    "seed": 0,
    "gpu": None,
    "fold": None,
    "weight_decay": 0,
    "step_size": None,
    "gamma": None,
    "num_warmup_epochs": None,
    "dataset_encoder" : DataSetEncoders.NONE,
    "metric_type" : MetricType.ACCURACY,
    'env_act_type': ActivationType.ELU,
    'act_type' : ActivationType.ELU
}

In [ ]:
CoGNN0 = CoGNN(params_cognn = params_cognn_relu).to(device)
train_model(CoGNN0, splits = 2)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.8367861, Val Loss: 0.7193253, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 002, LR: 0.001000, Train Loss: 0.7249098, Val Loss: 0.6934543, Test Acc: 0.5033333, Exp Acc: 0.4900000, Lrn Acc: 0.5000000, Train Acc: 0.4900000
Epoch: 003, LR: 0.001000, Train Loss: 0.7069077, Val Loss: 0.7037628, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 004, LR: 0.001000, Train Loss: 0.7082674, Val Loss: 0.7084785, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 005, LR: 0.001000, Train Loss: 0.7087010, Val Loss: 0.7024746, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.001000, Train Loss: 0.6991128, Val Loss: 0.6958848, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5033333, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.694158

In [ ]:
params_cognn_relu["env_dim"]= 32
params_cognn_relu["env_num_layers"]= 30
CoGNN0 = CoGNN(params_cognn = params_cognn_relu).to(device)
train_model(CoGNN0, splits = 2)


In [ ]:
params_cognn_elu = {
    "dataset": None,
    "pool": Pool.SUM,
    "learn_temp": False,
    "temp_model_type": ModelType.LIN,
    "tau0": 0.5,
    "temp": 0.5,
    "max_epochs": 3000,
    "batch_size": 20,
    "lr": 1e-3,
    "dropout": 0.2,
    "env_model_type": ModelType.SUM_GNN,
    "env_num_layers": 10,
    "env_dim": 128,
    "in_dim" : 2,
    'out_dim' : 2,
    "skip": False,
    "batch_norm": False,
    "layer_norm": pkl.FALSE,
    "dec_num_layers": 1,
    "pos_enc": PosEncoder.NONE,
    "act_model_type": ModelType.SUM_GNN,
    "act_num_layers": 1,
    "act_dim": 16,
    "seed": 0,
    "gpu": None,
    "fold": None,
    "weight_decay": 0,
    "step_size": None,
    "gamma": None,
    "num_warmup_epochs": None,
    "dataset_encoder" : DataSetEncoders.NONE,
    "metric_type" : MetricType.ACCURACY,
    'env_act_type': ActivationType.ELU,
    'act_type' : ActivationType.ELU
}

In [ ]:
for i in [0.001, 0.0001, 0.05,0.1,0.5]:
  for j in [0.0001,0.001,0.1]:
    for k in [1, 2, 3]:
      params_cognn_elu['temp'] = i
      params_cognn_elu['lr'] = j
      params_cognn_elu['act_num_layers'] = k
      CoGNN5 = CoGNN(params_cognn = params_cognn_elu).to(device)
      print(i,j,k)
      train_model(CoGNN5, epochs = 8, splits = 2)

0.001 0.0001 1
---------------- Split 0 ----------------


/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


Epoch: 001, LR: 0.001000, Train Loss: 7.4491291, Val Loss: 5.7552143, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 002, LR: 0.001000, Train Loss: 2.3606092, Val Loss: 0.8977101, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 003, LR: 0.001000, Train Loss: 1.2643770, Val Loss: 0.9598922, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 004, LR: 0.001000, Train Loss: 0.8811465, Val Loss: 1.1308857, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 005, LR: 0.001000, Train Loss: 1.2056405, Val Loss: 1.8843997, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 006, LR: 0.001000, Train Loss: 0.9595136, Val Loss: 1.2332797, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5000000, Train Acc: 0.5000000
Epoch: 007, LR: 0.001000, Train Loss: 0.9371803, Val Loss: 0.8337310, Test Acc: 0.500000

In [ ]:
params_cognn_elu = {
    "dataset": None,
    "pool": Pool.SUM,
    "learn_temp": 0.01,
    "temp_model_type": ModelType.LIN,
    "tau0": 0.5,
    "temp": 0.01,
    "max_epochs": 3000,
    "batch_size": 32,
    "lr": 1e-3,
    "dropout": 0.2,
    "env_model_type": ModelType.SUM_GNN,
    "env_num_layers": 8,
    "env_dim": 128,
    "in_dim" : 2,
    'out_dim' : 2,
    "skip": False,
    "batch_norm": False,
    "layer_norm": False,
    "dec_num_layers": 1,
    "pos_enc": PosEncoder.NONE,
    "act_model_type": ModelType.SUM_GNN,
    "act_num_layers": 1,
    "act_dim": 16,
    "seed": 0,
    "gpu": None,
    "fold": None,
    "weight_decay": 0,
    "step_size": None,
    "gamma": None,
    "num_warmup_epochs": None,
    "dataset_encoder" : DataSetEncoders.NONE,
    "metric_type" : MetricType.ACCURACY,
    'env_act_type': ActivationType.ELU,
    'act_type' : ActivationType.ELU
}

In [ ]:
CoGNN5 = CoGNN(params_cognn = params_cognn_elu).to(device)
CoGNN_results[40] = train_model(CoGNN5)

In [ ]:
CoGNN30 = CoGNN(params_cognn = params_cognn, rni = RNI_U30).to(device)
CoGNN_results[62] = train_model(CoGNN30)

In [ ]:
with open('CoGNN_results.pkl', 'wb') as pickle_file:
    pkl.dump(CoGNN_results, pickle_file)

In [ ]:
!python -u main.py -h

/usr/local/lib/python3.10/dist-packages/torch_geometric/graphgym/config.py:19: UserWarning: Could not define global config object. Please install 'yacs' via 'pip install yacs' in order to use GraphGym
  warnings.warn("Could not define global config object. Please install "
/usr/local/lib/python3.10/dist-packages/torch_geometric/graphgym/imports.py:14: UserWarning: Please install 'pytorch_lightning' via  'pip install pytorch_lightning' in order to use GraphGym
  warnings.warn("Please install 'pytorch_lightning' via  "
usage: main.py [-h]
               [--dataset {DataSet.roman_empire,DataSet.amazon_ratings,DataSet.minesweeper,DataSet.tolokers,DataSet.questions,DataSet.root_neighbours,DataSet.cycles,DataSet.exp,DataSet.imdb_binary,DataSet.imdb_multi,DataSet.reddit_binary,DataSet.enzymes,DataSet.proteins,DataSet.nci1,DataSet.func,DataSet.cora}]
               [--pool {Pool.NONE,Pool.MEAN,Pool.SUM}] [--learn_temp]
               [--temp_model_type {ModelType.GCN,ModelType.GIN,ModelType.LI

In [ ]:
!python -u main.py --dataset cycles --env_model_type MEAN_GNN --act_model_type MEAN_GNN --env_dim 64 --env_num_layers 3 --act_dim 16 --act_num_layers 1 --seed 0 --pool SUM --max_epochs 5000

/usr/local/lib/python3.10/dist-packages/torch_geometric/graphgym/config.py:19: UserWarning: Could not define global config object. Please install 'yacs' via 'pip install yacs' in order to use GraphGym
  warnings.warn("Could not define global config object. Please install "
/usr/local/lib/python3.10/dist-packages/torch_geometric/graphgym/imports.py:14: UserWarning: Please install 'pytorch_lightning' via  'pip install pytorch_lightning' in order to use GraphGym
  warnings.warn("Please install 'pytorch_lightning' via  "
dataset: DataSet.cycles
pool: Pool.SUM
learn_temp: False
temp_model_type: ModelType.LIN
tau0: 0.5
temp: 0.01
max_epochs: 5000
batch_size: 32
lr: 0.001
dropout: 0.2
env_model_type: ModelType.MEAN_GNN
env_num_layers: 3
env_dim: 64
skip: False
batch_norm: False
layer_norm: False
dec_num_layers: 1
pos_enc: PosEncoder.NONE
act_model_type: ModelType.MEAN_GNN
act_num_layers: 1
act_dim: 16
seed: 0
gpu: None
fold: None
weight_decay: 0
step_size: None
gamma: None
num_warmup_epochs: 

#DROGIN TEST

In [ ]:
dg_def = DropGIN(exp_dataset).to(device)
x = train_model(dg_def)

/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.9684251, Val Loss: 0.7869913, Test Acc: 0.5416667, Exp Acc: 0.5555556, Lrn Acc: 0.5407407, Train Acc: 0.5472222
Epoch: 002, LR: 0.001000, Train Loss: 0.5851568, Val Loss: 0.6016482, Test Acc: 0.6916667, Exp Acc: 0.6981481, Lrn Acc: 0.7037037, Train Acc: 0.6990741
Epoch: 003, LR: 0.001000, Train Loss: 0.2102815, Val Loss: 0.1129599, Test Acc: 0.9833333, Exp Acc: 0.9777778, Lrn Acc: 0.9777778, Train Acc: 0.9787037
Epoch: 004, LR: 0.001000, Train Loss: 0.2004923, Val Loss: 0.3100016, Test Acc: 0.8083333, Exp Acc: 0.8925926, Lrn Acc: 0.8740741, Train Acc: 0.8638889
Epoch: 005, LR: 0.001000, Train Loss: 0.1225596, Val Loss: 0.3251813, Test Acc: 0.8250000, Exp Acc: 0.8462963, Lrn Acc: 0.8296296, Train Acc: 0.8601852
Epoch: 006, LR: 0.001000, Train Loss: 0.0614863, Val Loss: 0.0609409, Test Acc: 0.9916667, Exp Acc: 0.9944444, Lrn Acc: 0.9944444, Train Acc: 0.9898148
Epoch: 007, LR: 0.001000, Train Loss: 0.026497

#Aggreagtion Architectures of rGIN

In [ ]:
rni30 = RNInit(random_dims = 30)
rGIN_sum30 = rGIN(rni = rni30, aggr = 'add').to(device)
rGIN_mean30 = rGIN(rni = rni30, aggr = 'mean').to(device)
rGIN_max30 = rGIN(aggr = 'max', rni =rni30).to(device)

In [ ]:
tr_accuracies_s, tst_accuracies_s, tst_exp_accuracies_s, tst_lrn_accuracies_s, acc_s, tr_acc_s  = train_model(rGIN_sum30, epochs = 700, splits = 5)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7134458, Val Loss: 0.7018761, Test Acc: 0.4958333, Exp Acc: 0.5020833, Lrn Acc: 0.4937500, Train Acc: 0.5052083
Epoch: 002, LR: 0.001000, Train Loss: 0.7007214, Val Loss: 0.7017833, Test Acc: 0.4625000, Exp Acc: 0.5145833, Lrn Acc: 0.5000000, Train Acc: 0.5114583
Epoch: 003, LR: 0.001000, Train Loss: 0.7044231, Val Loss: 0.6942144, Test Acc: 0.5458333, Exp Acc: 0.5166667, Lrn Acc: 0.4770833, Train Acc: 0.5135417
Epoch: 004, LR: 0.001000, Train Loss: 0.6969236, Val Loss: 0.6994597, Test Acc: 0.5000000, Exp Acc: 0.5020833, Lrn Acc: 0.4979167, Train Acc: 0.5020833
Epoch: 005, LR: 0.001000, Train Loss: 0.6947422, Val Loss: 0.6934421, Test Acc: 0.4875000, Exp Acc: 0.4916667, Lrn Acc: 0.5104167, Train Acc: 0.5406250
Epoch: 006, LR: 0.001000, Train Loss: 0.6947416, Val Loss: 0.6985662, Test Acc: 0.5041667, Exp Acc: 0.5041667, Lrn Acc: 0.5062500, Train Acc: 0.5145833
Epoch: 007, LR: 0.001000, Train Loss: 0.697545

In [ ]:
tr_accuracies_m, tst_accuracies_m, tst_exp_accuracies_m, tst_lrn_accuracies_m, acc_m, tr_acc_m  = train_model(rGIN_mean30, epochs = 700, splits = 5)

/usr/local/lib/python3.10/dist-packages/torch_geometric/deprecation.py:22: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)


---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7088706, Val Loss: 0.6985403, Test Acc: 0.4541667, Exp Acc: 0.5291667, Lrn Acc: 0.4958333, Train Acc: 0.5083333
Epoch: 002, LR: 0.001000, Train Loss: 0.7038153, Val Loss: 0.6982367, Test Acc: 0.5083333, Exp Acc: 0.5041667, Lrn Acc: 0.5041667, Train Acc: 0.4916667
Epoch: 003, LR: 0.001000, Train Loss: 0.7008613, Val Loss: 0.6945734, Test Acc: 0.4875000, Exp Acc: 0.5187500, Lrn Acc: 0.4854167, Train Acc: 0.4885417
Epoch: 004, LR: 0.001000, Train Loss: 0.7009227, Val Loss: 0.6938038, Test Acc: 0.5041667, Exp Acc: 0.5270833, Lrn Acc: 0.5166667, Train Acc: 0.5354167
Epoch: 005, LR: 0.001000, Train Loss: 0.7004050, Val Loss: 0.6969678, Test Acc: 0.4708333, Exp Acc: 0.5000000, Lrn Acc: 0.4770833, Train Acc: 0.4875000
Epoch: 006, LR: 0.001000, Train Loss: 0.6987063, Val Loss: 0.6942065, Test Acc: 0.5166667, Exp Acc: 0.5000000, Lrn Acc: 0.5041667, Train Acc: 0.5114583
Epoch: 007, LR: 0.001000, Train Loss: 0.697111

In [ ]:
tr_accuracies_x, tst_accuracies_x, tst_exp_accuracies_x, tst_lrn_accuracies_x, acc_x, tr_acc_x  = train_model(rGIN_max30, epochs = 700, splits = 5)

---------------- Split 0 ----------------
Epoch: 001, LR: 0.001000, Train Loss: 0.7156540, Val Loss: 0.6963225, Test Acc: 0.5250000, Exp Acc: 0.4958333, Lrn Acc: 0.5062500, Train Acc: 0.4781250
Epoch: 002, LR: 0.001000, Train Loss: 0.7024697, Val Loss: 0.6964711, Test Acc: 0.5416667, Exp Acc: 0.5145833, Lrn Acc: 0.4833333, Train Acc: 0.4968750
Epoch: 003, LR: 0.001000, Train Loss: 0.6986806, Val Loss: 0.6959032, Test Acc: 0.4708333, Exp Acc: 0.5312500, Lrn Acc: 0.5083333, Train Acc: 0.4875000
Epoch: 004, LR: 0.001000, Train Loss: 0.7016437, Val Loss: 0.6948382, Test Acc: 0.5000000, Exp Acc: 0.4958333, Lrn Acc: 0.5041667, Train Acc: 0.5031250
Epoch: 005, LR: 0.001000, Train Loss: 0.6957245, Val Loss: 0.6931462, Test Acc: 0.5083333, Exp Acc: 0.5020833, Lrn Acc: 0.4958333, Train Acc: 0.4885417
Epoch: 006, LR: 0.001000, Train Loss: 0.6935918, Val Loss: 0.6981607, Test Acc: 0.5000000, Exp Acc: 0.5000000, Lrn Acc: 0.5020833, Train Acc: 0.4989583
Epoch: 007, LR: 0.001000, Train Loss: 0.699501

#Functions For Visualizing

In [ ]:
    import matplot.lib as plt
    plt.figure(figsize=(10, 6))  # Set the figure size

    # Plot each array
    plt.plot(tst_accuracies_s, label='Sum')
    plt.plot(tst_accuracies_m, label='Mean')
    plt.plot(tst_accuracies_x, label='Max')

    # Add title and labels
    plt.title('Aggregation effect on rGIN learning')
    plt.xlabel('Epoch')
    plt.ylabel('Accuracy')

    # Add a legend
    plt.legend()
    plt.tight_layout()
    # Show the plot
    plt.savefig('summeanmaxplots.pdf')
    plt.show()

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-29-dadcdc0fac83>", line 1, in <cell line: 1>
    import matplot.lib as plt
  File "<frozen importlib._bootstrap>", line 1027, in _find_and_load
  File "<frozen importlib._bootstrap>", line 1002, in _find_and_load_unlocked
  File "<frozen importlib._bootstrap>", line 945, in _find_spec
  File "<frozen importlib._bootstrap_external>", line 1439, in find_spec
  File "<frozen importlib._bootstrap_external>", line 1408, in _get_spec
  File "<frozen importlib._bootstrap_external>", line 1366, in _path_importer_cache
OSError: [Errno 107] Transport endpoint is not connected

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/IPython/core/interactiveshell.py", line 2099, in showtra

In [ ]:
### Function to recover test accuracy from a .txt or a print
import re


def process_data(data_str):
    # Split the data into different splits
    splits = data_str.split('----------------')

    # List to hold all train accuracy arrays
    all_train_accs = []

    # Process each split
    for split in splits:
        # Find all occurrences of Train Acc and store them in a list
        train_accs = re.findall(r'Test Acc: (\d+\.\d+)', split)
        if train_accs:
            # Convert string values to float and append to the list
            all_train_accs.append([float(acc) for acc in train_accs])

    # Convert to numpy array for easy mean calculation
    all_train_accs_np = np.array(all_train_accs)

    # Check if the array is not empty and has consistent size
    if all_train_accs_np.size > 0 and len(set(map(len, all_train_accs_np))) == 1:
        # Calculate mean across all splits
        mean_train_acc = np.mean(all_train_accs_np, axis=0)
        return mean_train_acc
    else:
        return "Inconsistent data or empty input"